In [1]:
import warnings
warnings.filterwarnings('ignore')
import pandas as pd
import math
from sklearn.cross_validation import KFold
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.wordnet import WordNetLemmatizer
lemma=WordNetLemmatizer()
stop=set(stopwords.words('english'))
import seaborn as sns

C:\Users\sujith\Anaconda3\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
datafile_train=r'C:\Users\sujith\Desktop\Project\P1/Consumer_Complaints_train.csv'
datafile_test=r'C:\Users\sujith\Desktop\Project\P1/Consumer_Complaints_test_share.csv'
cd_train=pd.read_csv(datafile_train)
cd_test=pd.read_csv(datafile_test)

In [4]:
cd_train.head(10)

Date received                  Product                  Sub-product  \
0    2014-05-15              Credit card                          NaN   
1    2014-09-18  Bank account or service  (CD) Certificate of deposit   
2    2014-03-13         Credit reporting                          NaN   
3    2015-07-17              Credit card                          NaN   
4    2014-11-20              Credit card                          NaN   
5    2014-06-26                 Mortgage               Other mortgage   
6    2012-09-28                 Mortgage               Other mortgage   
7    2015-05-06                 Mortgage                 FHA mortgage   
8    2013-02-25              Credit card                          NaN   
9    2016-03-30  Bank account or service             Checking account   

                                      Issue       Sub-issue  \
0                         Billing statement             NaN   
1  Making/receiving payments, sending money             NaN   
2    Incorrect information on credit report  Account status   
3                         Billing statement             NaN   
4                         Transaction issue             NaN   
5  Loan modification,collection,foreclosure             NaN   
6  Loan servicing, payments, escrow account             NaN   
7  Loan modification,collection,foreclosure             NaN   
8  Credit card protection / Debt protection             NaN   
9                  Deposits and withdrawals             NaN   

                        Consumer complaint narrative  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3  My credit card statement from US Bank, XXXX. X...   
4                                                NaN   
5                                                NaN   
6                                                NaN   
7  I have a mortgage with Quicken Loans. From XXX...   
8                                                NaN   
9  I put my settlement check in to bank of americ...   

                             Company public response                Company  \
0                                                NaN  Wells Fargo & Company   
1                                                NaN      Santander Bank US   
2                                                NaN                Equifax   
3   Company chooses not to provide a public response           U.S. Bancorp   
4                                                NaN        Bank of America   
5                                                NaN        Bank of America   
6                                                NaN                  Ocwen   
7                                                NaN          Quicken Loans   
8                                                NaN               Discover   
9  Company has responded to the consumer and the ...        Bank of America   

  State ZIP code            Tags Consumer consent provided? Submitted via  \
0    MI    48342  Older American                        NaN           Web   
1    PA    18042             NaN                        NaN      Referral   
2    CA    92427             NaN                        NaN      Referral   
3    GA    305XX  Older American           Consent provided           Web   
4    MA    02127             NaN                        NaN           Web   
5    WI    54313             NaN                        NaN      Referral   
6    FL    33168             NaN                        NaN      Referral   
7    GA    300XX             NaN           Consent provided           Web   
8    OH    45640             NaN                        NaN           Web   
9    TX    787XX             NaN           Consent provided           Web   

  Date sent to company     Company response to consumer Timely response?  \
0           2014-05-16          Closed with explanation              Yes   
1           2014-

In [5]:
cd_train['Consumer disputed?']=np.where(cd_train['Consumer disputed?']=="Yes",0,1)

In [6]:
for col in ['Date received','Date sent to company']:
    cd_train[col]=pd.to_datetime(cd_train[col],infer_datetime_format=True)
    cd_test[col]=pd.to_datetime(cd_test[col],infer_datetime_format=True)

In [7]:
cd_train['day_diff']=pd.to_numeric((cd_train['Date sent to company']-cd_train['Date received'])/np.timedelta64(1, 'M'))
cd_test['day_diff']=pd.to_numeric((cd_test['Date sent to company']-cd_test['Date received'])/np.timedelta64(1, 'M'))

In [8]:
for col in ['Date received','Date sent to company']:
    cd_train.drop([col],1,inplace=True)
    cd_test.drop([col],1,inplace=True)

In [9]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Product : 12
Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company public response : 10
Company : 3276
State : 62
ZIP code : 25962
Tags : 3
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [10]:
for col in cd_test.select_dtypes(['object']).columns:
    print(col,':',cd_test[col].nunique())

Product : 12
Sub-product : 47
Issue : 94
Sub-issue : 67
Consumer complaint narrative : 18438
Company public response : 10
Company : 2237
State : 62
ZIP code : 17784
Tags : 3
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [11]:
cd_train['Tags'].value_counts()

Older American                   39064
Servicemember                    22592
Older American, Servicemember     5550
Name: Tags, dtype: int64

In [12]:
for col in cd_train['Tags']:
    print(col)

Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Servicemember
nan
Older American
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Servicemember
Older American
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American, 

nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Older American
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
Older American
nan


nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Servicemember
nan
nan
nan
Servicemember
Servicemember
nan
Older Americ

Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
Servicemember
nan
Older American
nan
nan
nan
nan
nan
Older American
Older American, Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older Ame

nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Servicemember
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
Older American
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
na

...

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American
nan
nan
Older American
Servicemember
Servicemember
nan
nan
na

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American, Servicemember
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
Older American
Older American
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
na

nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
Older American
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
Older American
nan
Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American, Servicemember
Servicemember
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Old

Older American
nan
nan
nan
Older American, Servicemember
Older American, Servicemember
nan
Older American
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Older American
nan
Older American
nan
nan
Older American, Servicemember
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
Servicemember
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Servicemember
Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Servicemember
Older American
nan
nan
Servicemember
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
n

In [13]:
cd_train.isnull().sum()

Product                              0
Sub-product                     138473
Issue                                0
Sub-issue                       292625
Consumer complaint narrative    403327
Company public response         388029
Company                              0
State                             3839
ZIP code                          3848
Tags                            411215
Consumer consent provided?      342934
Submitted via                        0
Company response to consumer         0
Timely response?                     0
Consumer disputed?                   0
Complaint ID                         0
day_diff                             0
dtype: int64

In [14]:
for col in ['Tags','Company public response']:
    varname=col.replace('-','_').replace('?','').replace(" ",'_')+'_isNan'
    cd_train[varname]=np.where(pd.isnull(cd_train[col]),1,0)
    cd_train.drop([col],1,inplace=True)
    cd_test[varname]=np.where(pd.isnull(cd_test[col]),1,0)
    cd_test.drop([col],1,inplace=True)
    

In [15]:
cd_train.dtypes

Product                           object
Sub-product                       object
Issue                             object
Sub-issue                         object
Consumer complaint narrative      object
Company                           object
State                             object
ZIP code                          object
Consumer consent provided?        object
Submitted via                     object
Company response to consumer      object
Timely response?                  object
Consumer disputed?                 int32
Complaint ID                       int64
day_diff                         float64
Tags_isNan                         int32
Company_public_response_isNan      int32
dtype: object

In [16]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Product : 12
Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company : 3276
State : 62
ZIP code : 25962
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [17]:
k=cd_train['State'].value_counts()
for val in k.axes[0][0:15]:
    varname='State_'+val.replace(',','_').replace(' ','_')
    cd_train[varname]=np.where(cd_train['State']==val,1,0)
    cd_test[varname]=np.where(cd_test['State']==val,1,0)
del cd_train['State']
del cd_test['State']

In [18]:
for col in ['Product','Submitted via','Company response to consumer','Timely response?']:
    
    temp=pd.get_dummies(cd_train[col],prefix=col,drop_first=True)
    cd_train=pd.concat([temp,cd_train],1)
    cd_train.drop([col],1,inplace=True)
    
    temp=pd.get_dummies(cd_test[col],prefix=col,drop_first=True)
    cd_test=pd.concat([temp,cd_test],1)
    cd_test.drop([col],1,inplace=True)


In [19]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company : 3276
ZIP code : 25962
Consumer consent provided? : 4


In [20]:
cd_train.shape

(478421, 50)

In [21]:
cd_test.shape

(119606, 49)

In [22]:
for col in ['ZIP code','Company']:
    cd_train.drop([col],1,inplace=True)
    cd_test.drop([col],1,inplace=True)

In [23]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Consumer consent provided? : 4


In [24]:
for col in cd_test.select_dtypes(['object']).columns:
    print(col,':',cd_test[col].nunique())

Sub-product : 47
Issue : 94
Sub-issue : 67
Consumer complaint narrative : 18438
Consumer consent provided? : 4


In [25]:
cd_train['Super']=cd_train['Consumer consent provided?']+cd_train['Sub-product']+cd_train['Issue']+','+cd_train['Sub-issue']+','+cd_train['Consumer complaint narrative']
del cd_train['Issue']
del cd_train['Sub-issue']
del cd_train['Consumer complaint narrative']
del cd_train['Consumer consent provided?']
cd_train["Super"]=np.where(pd.isnull(cd_train["Super"]),'NaN',cd_train['Super'])
cd_train['Super'].astype(str)
    

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
5         NaN
6         NaN
7         NaN
8         NaN
9         NaN
10        NaN
11        NaN
12        NaN
13        NaN
14        NaN
15        NaN
16        NaN
17        NaN
18        NaN
19        NaN
20        NaN
21        NaN
22        NaN
23        NaN
24        NaN
25        NaN
26        NaN
27        NaN
28        NaN
29        NaN
         ... 
478391    NaN
478392    NaN
478393    NaN
478394    NaN
478395    NaN
478396    NaN
478397    NaN
478398    NaN
478399    NaN
478400    NaN
478401    NaN
478402    NaN
478403    NaN
478404    NaN
478405    NaN
478406    NaN
478407    NaN
478408    NaN
478409    NaN
478410    NaN
478411    NaN
478412    NaN
478413    NaN
478414    NaN
478415    NaN
478416    NaN
478417    NaN
478418    NaN
478419    NaN
478420    NaN
Name: Super, Length: 478421, dtype: object

In [26]:
cd_test['Super']=cd_test['Consumer consent provided?']+cd_test['Sub-product']+cd_test['Issue']+','+cd_test['Sub-issue']+','+cd_test['Consumer complaint narrative']
del cd_test['Issue']
del cd_test['Sub-issue']
del cd_test['Consumer consent provided?']
del cd_test['Consumer complaint narrative']
cd_test["Super"]=np.where(pd.isnull(cd_test["Super"]),'NaN',cd_test['Super'])
cd_test['Super'].astype(str)
    

0                                                       NaN
1                                                       NaN
2                                                       NaN
3                                                       NaN
4                                                       NaN
5                                                       NaN
6                                                       NaN
7                                                       NaN
8                                                       NaN
9                                                       NaN
10                                                      NaN
11        Consent providedOther (i.e. phone, health club...
12                                                      NaN
13                                                      NaN
14                                                      NaN
15                                                      NaN
16                                      

In [27]:
cd_test.isnull().sum()

Timely response?_Yes                                                0
Company response to consumer_Closed with explanation                0
Company response to consumer_Closed with monetary relief            0
Company response to consumer_Closed with non-monetary relief        0
Company response to consumer_Closed with relief                     0
Company response to consumer_Closed without relief                  0
Company response to consumer_Untimely response                      0
Submitted via_Fax                                                   0
Submitted via_Phone                                                 0
Submitted via_Postal mail                                           0
Submitted via_Referral                                              0
Submitted via_Web                                                   0
Product_Consumer Loan                                               0
Product_Credit card                                                 0
Product_Credit repor

In [28]:
cd_train.isnull().sum()

Timely response?_Yes                                                 0
Company response to consumer_Closed with explanation                 0
Company response to consumer_Closed with monetary relief             0
Company response to consumer_Closed with non-monetary relief         0
Company response to consumer_Closed with relief                      0
Company response to consumer_Closed without relief                   0
Company response to consumer_Untimely response                       0
Submitted via_Fax                                                    0
Submitted via_Phone                                                  0
Submitted via_Postal mail                                            0
Submitted via_Referral                                               0
Submitted via_Web                                                    0
Product_Consumer Loan                                                0
Product_Credit card                                                  0
Produc

In [29]:
cd_train.head(4)

Timely response?_Yes  Company response to consumer_Closed with explanation  \
0                     1                                                  1      
1                     1                                                  0      
2                     1                                                  0      
3                     1                                                  0      

   Company response to consumer_Closed with monetary relief  \
0                                                  0          
1                                                  0          
2                                                  0          
3                                                  1          

   Company response to consumer_Closed with non-monetary relief  \
0                                                  0              
1                                                  0              
2                                                  1              
3                                                  0              

   Company response to consumer_Closed with relief  \
0                                                0   
1                                                0   
2                                                0   
3                                                0   

   Company response to consumer_Closed without relief  \
0                                                  0    
1                                                  0    
2                                                  0    
3                                                  0    

   Company response to consumer_Untimely response  Submitted via_Fax  \
0                                               0                  0   
1                                               0                  0   
2                                               0                  0   
3                                               0                  0   

   Submitted via_Phone  Submitted via_Postal mail  ...    State_PA  State_IL  \
0                    0                          0  ...           0         0   
1                    0                          0  ...           1         0   
2                    0                          0  ...           0         0   
3                    0                          0  ...           0         0   

   State_VA  State_MD  State_OH  State_NC  State_MI  State_AZ  State_WA  Super  
0         0         0         0         0         1         0         0    NaN  
1         0         0         0         0         0         0         0    NaN  
2         0         0         0         0         0         0         0    NaN  
3         0         0         0         0         0         0         0    NaN  

[4 rows x 45 columns]

In [30]:
cd_train['Super']

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
5         NaN
6         NaN
7         NaN
8         NaN
9         NaN
10        NaN
11        NaN
12        NaN
13        NaN
14        NaN
15        NaN
16        NaN
17        NaN
18        NaN
19        NaN
20        NaN
21        NaN
22        NaN
23        NaN
24        NaN
25        NaN
26        NaN
27        NaN
28        NaN
29        NaN
         ... 
478391    NaN
478392    NaN
478393    NaN
478394    NaN
478395    NaN
478396    NaN
478397    NaN
478398    NaN
478399    NaN
478400    NaN
478401    NaN
478402    NaN
478403    NaN
478404    NaN
478405    NaN
478406    NaN
478407    NaN
478408    NaN
478409    NaN
478410    NaN
478411    NaN
478412    NaN
478413    NaN
478414    NaN
478415    NaN
478416    NaN
478417    NaN
478418    NaN
478419    NaN
478420    NaN
Name: Super, Length: 478421, dtype: object

In [31]:
cd1_train,cd1_test=train_test_split(cd_train,test_size=0.2,random_state=2)

In [32]:
from sklearn.naive_bayes import MultinomialNB

In [33]:
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.wordnet import WordNetLemmatizer
lemma=WordNetLemmatizer()
stop=set(stopwords.words('english'))

In [34]:
def split_into_lemmas(message):
    words=word_tokenize(message)
    words_sans_stop=[]
    for word in words:
        if word in stop:continue
        words_sans_stop.append(word)
    return[lemma.lemmatize(word) for word in words_sans_stop]

In [35]:
tfidf=TfidfVectorizer(analyzer=split_into_lemmas,min_df=10,max_df=3000)

In [36]:
tfidf.fit(cd_train['Super'])

TfidfVectorizer(analyzer=<function split_into_lemmas at 0x0000009C0B1EC1E0>,
        binary=False, decode_error='strict', dtype=<class 'numpy.int64'>,
        encoding='utf-8', input='content', lowercase=True, max_df=3000,
        max_features=None, min_df=10, ngram_range=(1, 1), norm='l2',
        preprocessor=None, smooth_idf=True, stop_words=None,
        strip_accents=None, sublinear_tf=False,
        token_pattern='(?u)\\b\\w\\w+\\b', tokenizer=None, use_idf=True,
        vocabulary=None)

In [37]:
train_data=tfidf.transform(cd_train['Super'])

In [38]:
train_data

<478421x6924 sparse matrix of type '<class 'numpy.float64'>'
	with 1006357 stored elements in Compressed Sparse Row format>

In [39]:
test_data=tfidf.transform(cd_test['Super'])

In [40]:
clf=MultinomialNB()

In [41]:
clf.fit(train_data,cd_train['Consumer disputed?'])

MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True)

In [42]:
Final_data=tfidf.transform(cd_train['Super'])

In [43]:
p=clf.predict_proba(Final_data)

In [44]:
p.shape

(478421, 2)

In [45]:
p[:,0]

array([0.21201201, 0.21201201, 0.21201201, ..., 0.21201201, 0.21201201,
       0.21201201])

In [46]:
clf.classes_

array([0, 1])

In [47]:
cd_train['Tfidf']=np.where(p[:,0]>=0.5,0,1)

In [48]:
del cd_train['Super']

In [49]:
del cd_train['Sub-product']

In [50]:
Test_Final_data=tfidf.transform(cd_test['Super'])

In [51]:
Test_Final_data

<119606x6924 sparse matrix of type '<class 'numpy.float64'>'
	with 244916 stored elements in Compressed Sparse Row format>

In [52]:
r=clf.predict_proba(Test_Final_data)

In [53]:
r

array([[0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       ...,
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799]])

In [76]:
cd_test['Tfidf']=np.where(r[:,0]>=0.5,1,0)

In [77]:
del cd_test['Super']
del cd_test['Sub-product']

KeyError: 'Super'

In [ ]:
cd_train.dtypes

In [78]:
cd1_train,cd1_test=train_test_split(cd_train,test_size=0.2,random_state=2)

In [79]:
x=cd1_train.drop(['Consumer disputed?','Complaint ID'],1)
y=cd1_train['Consumer disputed?']
k=cd1_test.drop(['Consumer disputed?','Complaint ID'],1)
m=cd1_test['Consumer disputed?']


In [80]:
x.shape

(382736, 42)

In [81]:
m.value_counts()

1    75566
0    20119
Name: Consumer disputed?, dtype: int64

In [82]:
y.shape

(382736,)

In [83]:
m.shape

(95685,)

In [84]:
from sklearn.linear_model import LogisticRegression

In [85]:
clf=LogisticRegression()

In [86]:
clf.fit(x,y)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [87]:
prediction=clf.predict(k)

In [88]:
from sklearn.metrics import roc_auc_score

In [89]:
prediction

array([1, 1, 1, ..., 1, 1, 1])

In [90]:
m

154142    1
206525    0
26341     1
398527    1
134537    1
386176    0
264177    1
367070    1
241322    0
375399    1
20701     0
462090    1
350240    1
186458    1
416911    1
179519    0
215678    1
286383    0
239278    1
185495    1
85880     0
224145    1
28020     1
177179    1
31202     0
65934     1
211000    1
464440    1
70046     1
284961    0
         ..
351205    1
119688    0
149084    1
233584    1
131295    1
43415     1
152973    1
149762    0
271025    1
39276     1
353555    1
301445    1
105216    1
372933    1
31092     0
130094    0
474535    1
322547    1
193074    1
318770    1
353162    1
120328    1
400631    1
118418    1
337930    1
437699    1
325670    1
293448    0
317292    1
73745     0
Name: Consumer disputed?, Length: 95685, dtype: int32

In [91]:
roc_auc_score(prediction,m)

0.7183267931337731

In [92]:
prediction=np.where(clf.predict(cd_test.drop(['Complaint ID'],1))==1,"Yes","No")

In [93]:
prediction

array(['No', 'No', 'No', ..., 'No', 'No', 'No'], dtype='<U3')

In [94]:
submission=pd.DataFrame(list(zip(cd_test['Complaint ID'],list(prediction))),
                       columns=['Complaint ID','Consumer disputed?'])

In [95]:
m.value_counts()

1    75566
0    20119
Name: Consumer disputed?, dtype: int64

In [96]:
submission['Consumer disputed?'].value_counts()

No     97946
Yes    21660
Name: Consumer disputed?, dtype: int64

In [98]:
submission.to_csv('submission_final.csv',index=False)

In [97]:
cd_train['Consumer disputed?'].value_counts()

1    376990
0    101431
Name: Consumer disputed?, dtype: int64